In [1]:
from sqlalchemy import create_engine, text
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns
import geopandas as gpd
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from sklearn.metrics.pairwise import haversine_distances
from math import radians, sin, cos, sqrt, atan2
from geopy.distance import geodesic
import fiona
from shapely.geometry import Point
from geopy.geocoders import Nominatim

In [2]:
dtypes={'data_year': str,	'offense_id':str, 'incident_id':str,'offense_code': str,                                                                            'cargo_theft_flag': str, 'submission_date':str, 'incident_date':str,
        'attempt_complete_flag':str, 'location_id':str, 'cleared_except_id':str,'num_premises_entered':str,
        'method_entry_code':str}

al_crime = pd.read_csv('../data/crime/AL-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
ar_crime = pd.read_csv('../data/crime/AR-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
de_crime = pd.read_csv('../data/crime/DE-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
dc_crime = pd.read_csv('../data/crime/DC-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
fl_crime = pd.read_csv('../data/crime/FL-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
ga_crime = pd.read_csv('../data/crime/GA-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
ky_crime = pd.read_csv('../data/crime/KY-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
la_crime = pd.read_csv('../data/crime/LA-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
md_crime = pd.read_csv('../data/crime/MD-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
mo_crime = pd.read_csv('../data/crime/MO-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
ms_crime = pd.read_csv('../data/crime/MS-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
nc_crime = pd.read_csv('../data/crime/NC-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
oh_crime = pd.read_csv('../data/crime/OH-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
ok_crime = pd.read_csv('../data/crime/OK-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
pa_crime = pd.read_csv('../data/crime/PA-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
sc_crime = pd.read_csv('../data/crime/SC-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
tn_crime = pd.read_csv('../data/crime/TN-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
tx_crime = pd.read_csv('../data/crime/TX-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
va_crime = pd.read_csv('../data/crime/VA-2022/NIBRS_OFFENSE.csv',dtype=dtypes)
wv_crime = pd.read_csv('../data/crime/WV-2022/NIBRS_OFFENSE.csv',dtype=dtypes)


In [3]:

dtypes2={'data_year': str, 'agency_id':str, 'incident_id':str, 'nibrs_month_id':str, 'cargo_theft_flag':str, 'submission_date':str,
         'incident_date':str, 'report_date_flag':str, 'incident_hour':str, 'cleared_except_id':str,	'cleared_except_date':str,
         'incident_status':str,	'data_home':str, 'orig_format':str,	'did':str}
al_incident = pd.read_csv('../data/crime/AL-2022/NIBRS_incident.csv',dtype = dtypes2)
ar_incident = pd.read_csv('../data/crime/AR-2022/NIBRS_incident.csv',dtype = dtypes2)
de_incident = pd.read_csv('../data/crime/DE-2022/NIBRS_incident.csv',dtype = dtypes2)
dc_incident = pd.read_csv('../data/crime/DC-2022/NIBRS_incident.csv',dtype = dtypes2)
fl_incident = pd.read_csv('../data/crime/FL-2022/NIBRS_incident.csv',dtype = dtypes2)
ga_incident = pd.read_csv('../data/crime/GA-2022/NIBRS_incident.csv',dtype = dtypes2)
ky_incident = pd.read_csv('../data/crime/KY-2022/NIBRS_incident.csv',dtype = dtypes2)
la_incident = pd.read_csv('../data/crime/LA-2022/NIBRS_incident.csv',dtype = dtypes2)
md_incident = pd.read_csv('../data/crime/MD-2022/NIBRS_incident.csv',dtype = dtypes2)
mo_incident = pd.read_csv('../data/crime/MO-2022/NIBRS_incident.csv',dtype = dtypes2)
ms_incident = pd.read_csv('../data/crime/MS-2022/NIBRS_incident.csv',dtype = dtypes2)
nc_incident = pd.read_csv('../data/crime/NC-2022/NIBRS_incident.csv',dtype = dtypes2)
oh_incident = pd.read_csv('../data/crime/OH-2022/NIBRS_incident.csv',dtype = dtypes2)
ok_incident = pd.read_csv('../data/crime/OK-2022/NIBRS_incident.csv',dtype = dtypes2)
pa_incident = pd.read_csv('../data/crime/PA-2022/NIBRS_incident.csv',dtype = dtypes2)
sc_incident = pd.read_csv('../data/crime/SC-2022/NIBRS_incident.csv',dtype = dtypes2)
tn_incident = pd.read_csv('../data/crime/TN-2022/NIBRS_incident.csv',dtype = dtypes2)
tx_incident = pd.read_csv('../data/crime/TX-2022/NIBRS_incident.csv',dtype = dtypes2)
va_incident = pd.read_csv('../data/crime/VA-2022/NIBRS_incident.csv',dtype = dtypes2)
wv_incident = pd.read_csv('../data/crime/WV-2022/NIBRS_incident.csv',dtype = dtypes2)

In [24]:
dtypes3={'unitid':str, 'institution_name':str, 'year':int, 'HD2022.Historically Black College or University':str, 'agency_id':str,
         'campus_agency':str, 'city_agency':str, 'county_agency':str}
hbcu_list = pd.read_csv('../data/hbcu_list.csv', dtype=dtypes3)
hbcu_list.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 101 entries, 0 to 100
Data columns (total 8 columns):
 #   Column                                           Non-Null Count  Dtype 
---  ------                                           --------------  ----- 
 0   unitid                                           101 non-null    object
 1   institution_name                                 101 non-null    object
 2   year                                             101 non-null    int32 
 3   HD2022.Historically Black College or University  101 non-null    object
 4   agency_id                                        94 non-null     object
 5   campus_agency                                    100 non-null    object
 6   city_agency                                      98 non-null     object
 7   county_agency                                    98 non-null     object
dtypes: int32(1), object(7)
memory usage: 6.0+ KB


In [5]:
hbcu_list['agency_id'].unique()
agency_id_list=['360', '99', '263', '353', '51', '49', '23089', '235', '466',
       '450', '94', '23115', '728', '635', '729', '2268', '2243',
       '2615', '2920', '2539', '3693', '4189', '3995', '3776', '4028',
       '3771', '6675', '7269', '7204', '7295', '7171', '8020', '7926',
       '8029', '8079', '10200', '10207', '10313', '10306', '10174',
       '9621', '11202', '11438', '11077', '11335', '11524', '11204',
       '11118', '11607', '11135', '14382', '14372', '25368', '16403',
       '16203', '17892', '17904', '17860', '17975', '17498', '17944',
       '17871', '18271', '18513', '18747', '18295', '19756', '19856',
       '19869', '19800', '19871', '19413', '19678', '19870', '19284',
       '20431', '20448', '20437', '20453', '20460', '21572', '21494',
       '6807']

In [6]:
al_incident_f=al_incident.loc[al_incident['agency_id'].isin(agency_id_list)]
al_incident_f.reset_index()
ar_incident_f=ar_incident.loc[ar_incident['agency_id'].isin(agency_id_list)]
ar_incident_f.reset_index()
de_incident_f=de_incident.loc[de_incident['agency_id'].isin(agency_id_list)]
de_incident_f.reset_index()
dc_incident_f=dc_incident.loc[dc_incident['agency_id'].isin(agency_id_list)]
dc_incident_f.reset_index()
fl_incident_f=fl_incident.loc[fl_incident['agency_id'].isin(agency_id_list)]
fl_incident_f.reset_index()
ga_incident_f=ga_incident.loc[ga_incident['agency_id'].isin(agency_id_list)]
ga_incident_f.reset_index()
ky_incident_f=ky_incident.loc[ky_incident['agency_id'].isin(agency_id_list)]
ky_incident_f.reset_index()
la_incident_f=la_incident.loc[la_incident['agency_id'].isin(agency_id_list)]
la_incident_f.reset_index()
md_incident_f=md_incident.loc[md_incident['agency_id'].isin(agency_id_list)]
md_incident_f.reset_index()
mo_incident_f=mo_incident.loc[mo_incident['agency_id'].isin(agency_id_list)]
mo_incident_f.reset_index()
ms_incident_f=ms_incident.loc[ms_incident['agency_id'].isin(agency_id_list)]
ms_incident_f.reset_index()
nc_incident_f=nc_incident.loc[nc_incident['agency_id'].isin(agency_id_list)]
nc_incident_f.reset_index()
oh_incident_f=oh_incident.loc[oh_incident['agency_id'].isin(agency_id_list)]
oh_incident_f.reset_index()
ok_incident_f=ok_incident.loc[ok_incident['agency_id'].isin(agency_id_list)]
ok_incident_f.reset_index()
pa_incident_f=pa_incident.loc[pa_incident['agency_id'].isin(agency_id_list)]
pa_incident_f.reset_index()
sc_incident_f=sc_incident.loc[sc_incident['agency_id'].isin(agency_id_list)]
sc_incident_f.reset_index()
tn_incident_f=tn_incident.loc[tn_incident['agency_id'].isin(agency_id_list)]
tn_incident_f.reset_index()
tx_incident_f=tx_incident.loc[tx_incident['agency_id'].isin(agency_id_list)]
tx_incident_f.reset_index()
va_incident_f=va_incident.loc[va_incident['agency_id'].isin(agency_id_list)]
va_incident_f.reset_index()
wv_incident_f=wv_incident.loc[wv_incident['agency_id'].isin(agency_id_list)]
wv_incident_f.reset_index()

index data_year agency_id incident_id nibrs_month_id cargo_theft_flag  \
0    29414      2022     21494   150440041       44069296                f   
1    29415      2022     21494   150440057       44069296                f   
2    29418      2022     21494   159595021       44197993                f   
3    29434      2022     21494   159595036       44209677                f   
4    29435      2022     21494   161356818       44197993                f   
..     ...       ...       ...         ...            ...              ...   
256  35214      2022     21572   164059491       44257921                f   
257  35215      2022     21572   164059208       44257921                f   
258  35216      2022     21572   164059503       44257921                f   
259  35217      2022     21572   164059238       44257921                f   
260  35218      2022     21572   164059517       44257921                f   

             submission_date incident_date report_date_flag incident_hour  \
0    2022-03-11 13:14:31.495    2022-02-11                f             0   
1     2022-03-11 13:14:31.64    2022-02-23                f             0   
2    2022-10-11 12:13:31.772    2022-08-22                f             0   
3    2022-10-11 12:13:31.865    2022-09-03                f             0   
4     2022-11-10 18:19:41.91    2022-08-10                f             0   
..                       ...           ...              ...           ...   
256  2023-01-10 17:32:32.946    2022-12-19                f            16   
257  2023-01-10 17:32:29.265    2022-12-20                f            17   
258  2023-01-10 17:32:33.119    2022-12-20                f            13   
259  2023-01-10 17:32:29.628    2022-12-21                f             9   
260  2023-01-10 17:32:33.295    2022-12-31                f            11   

    cleared_except_id cleared_except_date incident_status data_home  \
0                   6                 NaN        ACCEPTED       NaN   
1                   6                 NaN        WARNINGS       NaN   
2                   6                 NaN        ACCEPTED       NaN   
3                   6                 NaN        ACCEPTED       NaN   
4                   6                 NaN        ACCEPTED       NaN   
..                ...                 ...             ...       ...   
256                 6                 NaN        ACCEPTED       NaN   
257                 6                 NaN        ACCEPTED       NaN   
258                 6                 NaN        ACCEPTED       NaN   
259                 6                 NaN        ACCEPTED       NaN   
260                 6                 NaN        ACCEPTED       NaN   

    orig_format        did  
0             F  133188986  
1             F  133189026  
2             F  157013038  
3             F  157013062  
4             F  161650528  
..          ...        ...  
256           F  168534209  
257           F  168533852  
258           F  168534227  
259           F  168533894  
260           F  168534239  

[261 rows x 16 columns]

In [7]:
dfs=[al_incident_f, ar_incident_f, de_incident_f, dc_incident_f, fl_incident_f, 
     ga_incident_f, ky_incident_f, la_incident_f, md_incident_f, mo_incident_f, 
     ms_incident_f, nc_incident_f, oh_incident_f, ok_incident_f, pa_incident_f,
     sc_incident_f, tn_incident_f, tx_incident_f, va_incident_f, wv_incident_f]
crime_dfs = pd.concat(dfs, axis=0, ignore_index=True)
crime_dfs

data_year agency_id incident_id nibrs_month_id cargo_theft_flag  \
0            2022        49   155372673       44169977                f   
1            2022        49   155377151       44169977                f   
2            2022        49   166585891       44303376                f   
3            2022        49   166584398       44303376                f   
4            2022        49   161106953       44209975                f   
...           ...       ...         ...            ...              ...   
1298431      2022     21572   164059491       44257921                f   
1298432      2022     21572   164059208       44257921                f   
1298433      2022     21572   164059503       44257921                f   
1298434      2022     21572   164059238       44257921                f   
1298435      2022     21572   164059517       44257921                f   

                 submission_date incident_date report_date_flag incident_hour  \
0          2022-07-06 13:41:03.8    2022-01-08                f            19   
1        2022-07-06 13:41:25.777    2022-01-22                f            21   
2         2023-02-14 14:44:55.98    2022-12-26                f            15   
3        2023-02-14 14:44:38.416    2022-12-16                f            20   
4        2022-11-04 20:20:25.003    2022-08-26                f            12   
...                          ...           ...              ...           ...   
1298431  2023-01-10 17:32:32.946    2022-12-19                f            16   
1298432  2023-01-10 17:32:29.265    2022-12-20                f            17   
1298433  2023-01-10 17:32:33.119    2022-12-20                f            13   
1298434  2023-01-10 17:32:29.628    2022-12-21                f             9   
1298435  2023-01-10 17:32:33.295    2022-12-31                f            11   

        cleared_except_id cleared_except_date incident_status data_home  \
0                       4          2022-01-08        WARNINGS       NaN   
1                       6                 NaN        ACCEPTED       NaN   
2                       6                 NaN        WARNINGS       NaN   
3                       6                 NaN        WARNINGS       NaN   
4                       6                 NaN        WARNINGS       NaN   
...                   ...                 ...             ...       ...   
1298431                 6                 NaN        ACCEPTED       NaN   
1298432                 6                 NaN        ACCEPTED       NaN   
1298433                 6                 NaN        ACCEPTED       NaN   
1298434                 6                 NaN        ACCEPTED       NaN   
1298435                 6                 NaN        ACCEPTED       NaN   

        orig_format        did  
0                 F  145967292  
1                 F  145974034  
2                 F  175090033  
3                 F  175088154  
4                 F  160996787  
...             ...        ...  
1298431           F  168534209  
1298432           F  168533852  
1298433           F  168534227  
1298434           F  168533894  
1298435           F  168534239  

[1298436 rows x 15 columns]

In [8]:
grouped_crimes= pd.merge(crime_dfs, hbcu_list, on=['agency_id'], how= 'left')
grouped_crimes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1597421 entries, 0 to 1597420
Data columns (total 22 columns):
 #   Column                                           Non-Null Count    Dtype 
---  ------                                           --------------    ----- 
 0   data_year                                        1597421 non-null  object
 1   agency_id                                        1597421 non-null  object
 2   incident_id                                      1597421 non-null  object
 3   nibrs_month_id                                   1597421 non-null  object
 4   cargo_theft_flag                                 1597421 non-null  object
 5   submission_date                                  1597421 non-null  object
 6   incident_date                                    1597421 non-null  object
 7   report_date_flag                                 1597421 non-null  object
 8   incident_hour                                    1596567 non-null  object
 9   cleared_excep

In [9]:
grouped_crimes1=grouped_crimes.loc[:,['institution_name','data_year', 'agency_id', 'incident_id',
                'campus_agency', 'city_agency', 'county_agency']]
grouped_crimes1

institution_name data_year agency_id incident_id  \
0                     Miles College      2022        49   155372673   
1                     Miles College      2022        49   155377151   
2                     Miles College      2022        49   166585891   
3                     Miles College      2022        49   166584398   
4                     Miles College      2022        49   161106953   
...                             ...       ...       ...         ...   
1597416  Bluefield State University      2022     21572   164059491   
1597417  Bluefield State University      2022     21572   164059208   
1597418  Bluefield State University      2022     21572   164059503   
1597419  Bluefield State University      2022     21572   164059238   
1597420  Bluefield State University      2022     21572   164059517   

        campus_agency city_agency county_agency  
0                   n           n             y  
1                   n           n             y  
2                   n           n             y  
3                   n           n             y  
4                   n           n             y  
...               ...         ...           ...  
1597416             n           y             n  
1597417             n           y             n  
1597418             n           y             n  
1597419             n           y             n  
1597420             n           y             n  

[1597421 rows x 7 columns]

In [10]:
grouped_crimes1.incident_id.info()

<class 'pandas.core.series.Series'>
RangeIndex: 1597421 entries, 0 to 1597420
Series name: incident_id
Non-Null Count    Dtype 
--------------    ----- 
1597421 non-null  object
dtypes: object(1)
memory usage: 12.2+ MB


In [11]:
al_crime_incident = al_crime.loc[al_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
ar_crime_incident = ar_crime.loc[ar_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
de_crime_incident = de_crime.loc[de_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
dc_crime_incident = dc_crime.loc[dc_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
fl_crime_incident = fl_crime.loc[fl_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
ga_crime_incident = ga_crime.loc[ga_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
ky_crime_incident = ky_crime.loc[ky_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
la_crime_incident = la_crime.loc[la_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
md_crime_incident = md_crime.loc[md_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
mo_crime_incident = mo_crime.loc[mo_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
ms_crime_incident = ms_crime.loc[ms_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
nc_crime_incident = nc_crime.loc[nc_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
oh_crime_incident = oh_crime.loc[oh_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
ok_crime_incident = ok_crime.loc[ok_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
pa_crime_incident = pa_crime.loc[pa_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
sc_crime_incident = sc_crime.loc[sc_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
tn_crime_incident = tn_crime.loc[tn_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
tx_crime_incident = tx_crime.loc[tx_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
va_crime_incident = va_crime.loc[va_crime['incident_id'].isin(grouped_crimes1['incident_id'])]
wv_crime_incident = wv_crime.loc[wv_crime['incident_id'].isin(grouped_crimes1['incident_id'])]

In [12]:
dfs2=[al_crime_incident, ar_crime_incident, de_crime_incident, dc_crime_incident,
     fl_crime_incident, ga_crime_incident, ky_crime_incident, la_crime_incident, 
     md_crime_incident, mo_crime_incident, ms_crime_incident, nc_crime_incident, 
     oh_crime_incident, ok_crime_incident, pa_crime_incident, sc_crime_incident, 
     tn_crime_incident, tx_crime_incident, va_crime_incident, wv_crime_incident]
crimes_dfs = pd.concat(dfs2, axis=0, ignore_index=True)
crimes_dfs

data_year offense_id incident_id offense_code attempt_complete_flag  \
0            2022  185984862   155372673          520                     C   
1            2022  185984863   155372673          35B                     C   
2            2022  185984864   155372673          35A                     C   
3            2022  185990229   155377151          13B                     C   
4            2022  198846184   166585891          23D                     C   
...           ...        ...         ...          ...                   ...   
1443287      2022  195960036   164059491          290                     C   
1443288      2022  195959724   164059208          13B                     C   
1443289      2022  195960050   164059503          13B                     C   
1443290      2022  195959760   164059238          13B                     C   
1443291      2022  195960066   164059517          35A                     C   

        location_id num_premises_entered method_entry_code  
0                25                  NaN               NaN  
1                25                  NaN               NaN  
2                25                  NaN               NaN  
3                35                  NaN               NaN  
4                35                  NaN               NaN  
...             ...                  ...               ...  
1443287          25                  NaN               NaN  
1443288          35                  NaN               NaN  
1443289          23                  NaN               NaN  
1443290          35                  NaN               NaN  
1443291          33                  NaN               NaN  

[1443292 rows x 8 columns]

In [13]:
crimes_incident=  pd.merge(grouped_crimes1, crimes_dfs, on=['incident_id'], how= 'left')
crimes_incident

institution_name data_year_x agency_id incident_id  \
0                     Miles College        2022        49   155372673   
1                     Miles College        2022        49   155372673   
2                     Miles College        2022        49   155372673   
3                     Miles College        2022        49   155377151   
4                     Miles College        2022        49   166585891   
...                             ...         ...       ...         ...   
1785024  Bluefield State University        2022     21572   164059491   
1785025  Bluefield State University        2022     21572   164059208   
1785026  Bluefield State University        2022     21572   164059503   
1785027  Bluefield State University        2022     21572   164059238   
1785028  Bluefield State University        2022     21572   164059517   

        campus_agency city_agency county_agency data_year_y offense_id  \
0                   n           n             y        2022  185984862   
1                   n           n             y        2022  185984863   
2                   n           n             y        2022  185984864   
3                   n           n             y        2022  185990229   
4                   n           n             y        2022  198846184   
...               ...         ...           ...         ...        ...   
1785024             n           y             n        2022  195960036   
1785025             n           y             n        2022  195959724   
1785026             n           y             n        2022  195960050   
1785027             n           y             n        2022  195959760   
1785028             n           y             n        2022  195960066   

        offense_code attempt_complete_flag location_id num_premises_entered  \
0                520                     C          25                  NaN   
1                35B                     C          25                  NaN   
2                35A                     C          25                  NaN   
3                13B                     C          35                  NaN   
4                23D                     C          35                  NaN   
...              ...                   ...         ...                  ...   
1785024          290                     C          25                  NaN   
1785025          13B                     C          35                  NaN   
1785026          13B                     C          23                  NaN   
1785027          13B                     C          35                  NaN   
1785028          35A                     C          33                  NaN   

        method_entry_code  
0                     NaN  
1                     NaN  
2                     NaN  
3                     NaN  
4                     NaN  
...                   ...  
1785024               NaN  
1785025               NaN  
1785026               NaN  
1785027               NaN  
1785028               NaN  

[1785029 rows x 14 columns]

In [14]:
crimes_incident= crimes_incident.loc[:,['institution_name','offense_id', 'incident_id',
                                        'offense_code','campus_agency',	'city_agency', 
                                        'county_agency']]
crimes_incident

institution_name offense_id incident_id offense_code  \
0                     Miles College  185984862   155372673          520   
1                     Miles College  185984863   155372673          35B   
2                     Miles College  185984864   155372673          35A   
3                     Miles College  185990229   155377151          13B   
4                     Miles College  198846184   166585891          23D   
...                             ...        ...         ...          ...   
1785024  Bluefield State University  195960036   164059491          290   
1785025  Bluefield State University  195959724   164059208          13B   
1785026  Bluefield State University  195960050   164059503          13B   
1785027  Bluefield State University  195959760   164059238          13B   
1785028  Bluefield State University  195960066   164059517          35A   

        campus_agency city_agency county_agency  
0                   n           n             y  
1                   n           n             y  
2                   n           n             y  
3                   n           n             y  
4                   n           n             y  
...               ...         ...           ...  
1785024             n           y             n  
1785025             n           y             n  
1785026             n           y             n  
1785027             n           y             n  
1785028             n           y             n  

[1785029 rows x 7 columns]

In [15]:
institution_off_code= crimes_incident.groupby(['institution_name','offense_code']).size()
institution_off_codes=institution_off_code.to_frame(name='off_code_count')
institution_off_codes=institution_off_codes.reset_index()

In [18]:
institution_off_codes= institution_off_codes.sort_values(by=['institution_name', 'off_code_count'], ascending=[True, False])
institution_off_codes= institution_off_codes.reset_index()

institution_name offense_code  off_code_count
10          Alabama A & M University          290              15
1           Alabama A & M University          13B              14
2           Alabama A & M University          13C              10
3           Alabama A & M University          220               9
7           Alabama A & M University          23H               8
...                              ...          ...             ...
2640  Winston-Salem State University          09C               2
2665  Winston-Salem State University          26E               2
2639  Winston-Salem State University          09B               1
2667  Winston-Salem State University          26G               1
2677  Winston-Salem State University          40B               1

[2680 rows x 3 columns]

In [25]:
hbcu_list

unitid                                   institution_name  year  \
0    100654                           Alabama A & M University  2022   
1    100724                           Alabama State University  2022   
2    101240                    Gadsden State Community College  2022   
3    101462  J. F. Drake State Community and Technical College  2022   
4    101569                     Lawson State Community College  2022   
..      ...                                                ...   ...   
96   237215                         Bluefield State University  2022   
97   237899                     West Virginia State University  2022   
98   243665                   University of the Virgin Islands  2022   
99   440916                     Southern University Law Center  2022   
100  461759                        Simmons College of Kentucky  2022   

    HD2022.Historically Black College or University agency_id campus_agency  \
0                                               Yes       360             y   
1                                               Yes        99             y   
2                                               Yes       263             n   
3                                               Yes       353             n   
4                                               Yes        51             y   
..                                              ...       ...           ...   
96                                              Yes     21572             n   
97                                              Yes     21494             y   
98                                              Yes       NaN           NaN   
99                                              Yes      7204             n   
100                                             Yes      6807             n   

    city_agency county_agency  
0             n             n  
1             n             n  
2             y             n  
3             y             n  
4             n             n  
..          ...           ...  
96            y             n  
97            n             n  
98          NaN           NaN  
99            y             n  
100           y             n  

[101 rows x 8 columns]

In [36]:
campus_count=hbcu_list['campus_agency'].value_counts()['y']
campus_count

30

In [37]:
city_count=hbcu_list['city_agency'].value_counts()['y']
city_count

52

In [38]:
county_count=hbcu_list['county_agency'].value_counts()['y']
county_count

12

In [39]:
institution_off_codes= institution_off_codes.reset_index()
institution_off_codes

index                institution_name offense_code  off_code_count
0        10        Alabama A & M University          290              15
1         1        Alabama A & M University          13B              14
2         2        Alabama A & M University          13C              10
3         3        Alabama A & M University          220               9
4         7        Alabama A & M University          23H               8
...     ...                             ...          ...             ...
2675   2640  Winston-Salem State University          09C               2
2676   2665  Winston-Salem State University          26E               2
2677   2639  Winston-Salem State University          09B               1
2678   2667  Winston-Salem State University          26G               1
2679   2677  Winston-Salem State University          40B               1

[2680 rows x 4 columns]

In [41]:
institution_off_codes=institution_off_codes.drop(institution_off_codes.columns[0], axis=1)
institution_off_codes

institution_name offense_code  off_code_count
0           Alabama A & M University          290              15
1           Alabama A & M University          13B              14
2           Alabama A & M University          13C              10
3           Alabama A & M University          220               9
4           Alabama A & M University          23H               8
...                              ...          ...             ...
2675  Winston-Salem State University          09C               2
2676  Winston-Salem State University          26E               2
2677  Winston-Salem State University          09B               1
2678  Winston-Salem State University          26G               1
2679  Winston-Salem State University          40B               1

[2680 rows x 3 columns]

In [42]:
pd.set_option('display.max_rows', None)
institution_off_codes

institution_name offense_code  \
0                              Alabama A & M University          290   
1                              Alabama A & M University          13B   
2                              Alabama A & M University          13C   
3                              Alabama A & M University          220   
4                              Alabama A & M University          23H   
5                              Alabama A & M University          35A   
6                              Alabama A & M University          26B   
7                              Alabama A & M University          23D   
8                              Alabama A & M University          23F   
9                              Alabama A & M University          35B   
10                             Alabama A & M University          13A   
11                             Alabama A & M University          520   
12                             Alabama A & M University          23G   
13                             Alabama A & M University          26F   
14                             Alabama State University          13B   
15                              Albany State University          13B   
16                              Albany State University          23H   
17                              Albany State University          13A   
18                              Albany State University          23C   
19                              Albany State University          240   
20                              Albany State University          13C   
21                              Albany State University          23F   
22                              Albany State University          220   
23                              Albany State University          23G   
24                              Albany State University          290   
25                              Albany State University          26A   
26                              Albany State University          09A   
27                              Albany State University          11D   
28                              Albany State University          11A   
29                              Albany State University          120   
30                              Albany State University          250   
31                              Albany State University          200   
32                              Albany State University          11B   
33                              Albany State University          26B   
34                              Albany State University          35A   
35                              Albany State University          36B   
36                              Albany State University          280   
37                              Albany State University          520   
38                              Alcorn State University          13A   
39                              Alcorn State University          13B   
40                              Alcorn State University          220   
41                              Alcorn State University          23F   
42                              Alcorn State University          23H   
43                              Alcorn State University          240   
44                              Alcorn State University          520   
45                              Alcorn State University          26E   
46                              Alcorn State University          09A   
47                              Alcorn State University          09B   
48                              Alcorn State University          11A   
49                              Alcorn State University          120   
50                              Alcorn State University          13C   
51                              Alcorn State University          290   
52                                     Allen University          290   
53                                     Allen University          23H   
54                                     Allen University          23F   
55     

In [47]:
off_code_name=pd.read_csv("../data/crime/AL-2022/NIBRS_OFFENSE_TYPE.csv")
institutions_off_codes=  pd.merge(institution_off_codes, off_code_name, on=['offense_code'], how= 'left')
institutions_off_codes

institution_name offense_code  \
0                              Alabama A & M University          290   
1                              Alabama A & M University          13B   
2                              Alabama A & M University          13C   
3                              Alabama A & M University          220   
4                              Alabama A & M University          23H   
5                              Alabama A & M University          35A   
6                              Alabama A & M University          26B   
7                              Alabama A & M University          23D   
8                              Alabama A & M University          23F   
9                              Alabama A & M University          35B   
10                             Alabama A & M University          13A   
11                             Alabama A & M University          520   
12                             Alabama A & M University          23G   
13                             Alabama A & M University          26F   
14                             Alabama State University          13B   
15                              Albany State University          13B   
16                              Albany State University          23H   
17                              Albany State University          13A   
18                              Albany State University          23C   
19                              Albany State University          240   
20                              Albany State University          13C   
21                              Albany State University          23F   
22                              Albany State University          220   
23                              Albany State University          23G   
24                              Albany State University          290   
25                              Albany State University          26A   
26                              Albany State University          09A   
27                              Albany State University          11D   
28                              Albany State University          11A   
29                              Albany State University          120   
30                              Albany State University          250   
31                              Albany State University          200   
32                              Albany State University          11B   
33                              Albany State University          26B   
34                              Albany State University          35A   
35                              Albany State University          36B   
36                              Albany State University          280   
37                              Albany State University          520   
38                              Alcorn State University          13A   
39                              Alcorn State University          13B   
40                              Alcorn State University          220   
41                              Alcorn State University          23F   
42                              Alcorn State University          23H   
43                              Alcorn State University          240   
44                              Alcorn State University          520   
45                              Alcorn State University          26E   
46                              Alcorn State University          09A   
47                              Alcorn State University          09B   
48                              Alcorn State University          11A   
49                              Alcorn State University          120   
50                              Alcorn State University          13C   
51                              Alcorn State University          290   
52                                     Allen University          290   
53                                     Allen University          23H   
54                                     Allen University          23F   
55     

In [49]:
institutions_off_codes=institutions_off_codes[['institution_name','offense_code', 'off_code_count', 'offense_name', 
                                               'crime_against', 'offense_category_name']]
institutions_off_codes

institution_name offense_code  \
0                              Alabama A & M University          290   
1                              Alabama A & M University          13B   
2                              Alabama A & M University          13C   
3                              Alabama A & M University          220   
4                              Alabama A & M University          23H   
5                              Alabama A & M University          35A   
6                              Alabama A & M University          26B   
7                              Alabama A & M University          23D   
8                              Alabama A & M University          23F   
9                              Alabama A & M University          35B   
10                             Alabama A & M University          13A   
11                             Alabama A & M University          520   
12                             Alabama A & M University          23G   
13                             Alabama A & M University          26F   
14                             Alabama State University          13B   
15                              Albany State University          13B   
16                              Albany State University          23H   
17                              Albany State University          13A   
18                              Albany State University          23C   
19                              Albany State University          240   
20                              Albany State University          13C   
21                              Albany State University          23F   
22                              Albany State University          220   
23                              Albany State University          23G   
24                              Albany State University          290   
25                              Albany State University          26A   
26                              Albany State University          09A   
27                              Albany State University          11D   
28                              Albany State University          11A   
29                              Albany State University          120   
30                              Albany State University          250   
31                              Albany State University          200   
32                              Albany State University          11B   
33                              Albany State University          26B   
34                              Albany State University          35A   
35                              Albany State University          36B   
36                              Albany State University          280   
37                              Albany State University          520   
38                              Alcorn State University          13A   
39                              Alcorn State University          13B   
40                              Alcorn State University          220   
41                              Alcorn State University          23F   
42                              Alcorn State University          23H   
43                              Alcorn State University          240   
44                              Alcorn State University          520   
45                              Alcorn State University          26E   
46                              Alcorn State University          09A   
47                              Alcorn State University          09B   
48                              Alcorn State University          11A   
49                              Alcorn State University          120   
50                              Alcorn State University          13C   
51                              Alcorn State University          290   
52                                     Allen University          290   
53                                     Allen University          23H   
54                                     Allen University          23F   
55     

In [50]:
institutions_off_codes.offense_name.unique()

array(['Destruction/Damage/Vandalism of Property', 'Simple Assault',
       'Intimidation', 'Burglary/Breaking & Entering',
       'All Other Larceny', 'Drug/Narcotic Violations',
       'Credit Card/Automated Teller Machine Fraud',
       'Theft From Building', 'Theft From Motor Vehicle',
       'Drug Equipment Violations', 'Aggravated Assault',
       'Weapon Law Violations',
       'Theft of Motor Vehicle Parts or Accessories', 'Identity Theft',
       'Shoplifting', 'Motor Vehicle Theft',
       'False Pretenses/Swindle/Confidence Game',
       'Murder and Nonnegligent Manslaughter', 'Fondling', 'Rape',
       'Robbery', 'Counterfeiting/Forgery', 'Arson', 'Sodomy',
       'Statutory Rape', 'Stolen Property Offenses', 'Wire Fraud',
       'Negligent Manslaughter', 'Kidnapping/Abduction',
       'Extortion/Blackmail', 'Purse-snatching', 'Welfare Fraud',
       'Theft From Coin-Operated Machine or Device', 'Pocket-picking',
       'Impersonation', 'Betting/Wagering', 'Justifiable Homi